In [2]:
!pip install geocoder
!pip install folium
!pip install shapely
!pip install pyproj

     |████████████████████████████████| 98 kB 9.0 MB/s  eta 0:00:01
     |████████████████████████████████| 94 kB 6.1 MB/s  eta 0:00:01
     |████████████████████████████████| 1.0 MB 14.6 MB/s eta 0:00:01
     |████████████████████████████████| 6.5 MB 12.8 MB/s eta 0:00:01


In [3]:
import pandas as pd # library for data analsysis
import requests # library to handle requests
import numpy as np # library to handle data in a vectorized manner
import geocoder
import folium # map rendering library
import matplotlib.cm as cm # Matplotlib and associated plotting modules
import matplotlib.colors as colors # Matplotlib and associated plotting modules
import json # library to handle JSON files

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe
from sklearn.cluster import KMeans # import k-means from clustering stage
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
from bs4 import BeautifulSoup

import shapely.geometry
from pyproj import Transformer 
import math

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

print("All Required Libraries Imported!")

All Required Libraries Imported!


In [4]:
!wget -q -O 'newyork_data.json' https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json
print('Data downloaded!')

Data downloaded!


In [5]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [6]:
neighborhoods_data = newyork_data['features']

In [7]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [8]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [9]:
neighborhoods

Borough               Neighborhood   Latitude  Longitude
0            Bronx                  Wakefield  40.894705 -73.847201
1            Bronx                 Co-op City  40.874294 -73.829939
2            Bronx                Eastchester  40.887556 -73.827806
3            Bronx                  Fieldston  40.895437 -73.905643
4            Bronx                  Riverdale  40.890834 -73.912585
5            Bronx                Kingsbridge  40.881687 -73.902818
6        Manhattan                Marble Hill  40.876551 -73.910660
7            Bronx                   Woodlawn  40.898273 -73.867315
8            Bronx                    Norwood  40.877224 -73.879391
9            Bronx             Williamsbridge  40.881039 -73.857446
10           Bronx                 Baychester  40.866858 -73.835798
11           Bronx             Pelham Parkway  40.857413 -73.854756
12           Bronx                City Island  40.847247 -73.786488
13           Bronx               Bedford Park  40.870185 -73.885512
14           Bronx         University Heights  40.855727 -73.910416
15           Bronx             Morris Heights  40.847898 -73.919672
16           Bronx                    Fordham  40.860997 -73.896427
17           Bronx               East Tremont  40.842696 -73.887356
18           Bronx                 West Farms  40.839475 -73.877745
19           Bronx               High  Bridge  40.836623 -73.926102
20           Bronx                    Melrose  40.819754 -73.909422
21           Bronx                 Mott Haven  40.806239 -73.916100
22           Bronx                Port Morris  40.801664 -73.913221
23           Bronx                   Longwood  40.815099 -73.895788
24           Bronx                Hunts Point  40.809730 -73.883315
25           Bronx                 Morrisania  40.823592 -73.901506
26           Bronx                  Soundview  40.821012 -73.865746
27           Bronx               Clason Point  40.806551 -73.854144
28           Bronx                Throgs Neck  40.815109 -73.816350
29           Bronx               Country Club  40.844246 -73.824099
30           Bronx                Parkchester  40.837938 -73.856003
31           Bronx         Westchester Square  40.840619 -73.842194
32           Bronx                   Van Nest  40.843608 -73.866299
33           Bronx                Morris Park  40.847549 -73.850402
34           Bronx                    Belmont  40.857277 -73.888452
35           Bronx             Spuyten Duyvil  40.881395 -73.917190
36           Bronx            North Riverdale  40.908543 -73.904531
37           Bronx                 Pelham Bay  40.850641 -73.832074
38           Bronx              Schuylerville  40.826580 -73.826203
39           Bronx             Edgewater Park  40.821986 -73.813885
40           Bronx                Castle Hill  40.819014 -73.848027
41           Bronx                  Olinville  40.871371 -73.863324
42           Bronx             Pelham Gardens  40.862966 -73.841612
43           Bronx                  Concourse  40.834284 -73.915589
44           Bronx                  Unionport  40.829774 -73.850535
45           Bronx                   Edenwald  40.884561 -73.848083
46        Brooklyn                  Bay Ridge  40.625801 -74.030621
47        Brooklyn                Bensonhurst  40.611009 -73.995180
48        Brooklyn                Sunset Park  40.645103 -74.010316
49        Brooklyn                 Greenpoint  40.730201 -73.954241
50        Brooklyn                  Gravesend  40.595260 -73.973471
51        Brooklyn             Brighton Beach  40.576825 -73.965094
52        Brooklyn             Sheepshead Bay  40.586890 -73.943186
53        Brooklyn          Manhattan Terrace  40.614433 -73.957438
54        Brooklyn                   Flatbush  40.636326 -73.958401
55        Brooklyn              Crown Heights  40.670829 -73.943291
56        Brooklyn              East Flatbush  40.641718 -73.936103
57        Brooklyn                 Kensington  40.642382 -73.980421

In [10]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


In [11]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [12]:
def lonlat_to_xy(lon, lat):
    transproj = Transformer.from_crs({"proj":'latlong', "datum":'WGS84'}, {"proj":'utm', "zone":'33', "datum":'WGS84'})
    xy = transproj.transform(lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    transproj = Transformer.from_crs({"proj":'utm', "zone":'33', "datum":'WGS84'}, {"proj":'latlong', "datum":'WGS84'})
    lonlat = transproj.transform(x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Berlin center longitude={}, latitude={}'.format(longitude, latitude))
x, y = lonlat_to_xy(longitude, latitude)
print('Berlin center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Berlin center longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Berlin center longitude=-74.0060152, latitude=40.7127281
Berlin center UTM X=-5822290.638374001, Y=9869604.759469567
Berlin center longitude=-74.00601519999961, latitude=40.71272809999887


In [13]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [14]:
# Category IDs corresponding to japanese restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4bf58dd8d48988d142941735' # 'Root' category for all food-related venues

japanese_restaurant_categories = '4bf58dd8d48988d111941735'

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius, limit):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [15]:
import pickle

foursquare_client_id = 'DPBYY4JUY3DU20ALPSUV4ONY2K1GOJJKJ1NIHBB32XEMOVYY'
foursquare_client_secret = '1MV443TYEP4HUO0WDUW5NQ5W10L2Y4G05NWG11WIR3NUGC5B'

def get_restaurants(lats, lons):
    restaurants = {}
    japanese_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        venues = get_venues_near_location(lat, lon, food_category, foursquare_client_id, foursquare_client_secret, radius=350, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res, is_japanese = is_restaurant(venue_categories, specific_filter=japanese_restaurant_categories)
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_japanese, x, y)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_japanese:
                    japanese_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, japanese_restaurants, location_restaurants

In [16]:
restaurants, japanese_restaurants, location_restaurants = get_restaurants(neighborhoods['Latitude'], neighborhoods['Longitude'])

Obtaining venues around candidate locations: . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [17]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Total number of japanese restaurants:', len(japanese_restaurants))
print('Percentage of japanese restaurants: {:.2f}%'.format(len(japanese_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 1820
Total number of japanese restaurants: 193
Percentage of japanese restaurants: 10.60%
Average number of restaurants in neighborhood: 4.598039215686274


In [18]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('4c9d5f2654c8a1cd2e71834b', 'Guang Hui Chinese Restaurant', 40.876651, -73.829092, '125 Dreiser Loop, Bronx, NY 10475, United States', 271, False, -5793874.137036882, 9847632.08621121)
('4dabc3dc93a04642f09ccabd', 'Xing Lung Chinese Restaurant', 40.8887854684858, -73.83122576835156, '3828 B Dyre Ave (E 233 St), Bronx, NY 10466, United States', 318, False, -5791831.3721499685, 9847969.520214086)
('4e4ddf76bd4101d0d79d3e83', 'Panda Restaurant', 40.880013, -73.90440799999999, '5625 Broadway, Bronx, NY 10463, United States', 229, False, -5793596.3873716025, 9857314.032258978)
('4b2285c5f964a520454824e3', 'Pioneer Chinese Restaurant', 40.879540999999996, -73.905327, '223 W 231st St (btwn Broadway and Godwin), Bronx, NY 10463, United States', 318, False, -5793679.615418206, 9857429.642567653)
('4c703518b5a5236a2d934f52', 'Kam Wah Kitchen', 40.87608431180527, -73.90869825954931, '5400 Broadway, Bronx, NY 10463, United States', 173, False, -5794

In [19]:
print('List of japanese restaurants')
print('---------------------------')
for r in list(japanese_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(japanese_restaurants))

List of japanese restaurants
---------------------------
('4ed9459702d5244e2f1ade7c', 'Empire Chinese And Japanese Cuisine', 40.878588, -73.917446, 'Bronx, NY 10463, United States', 313, True, -5793885.6690578945, 9858980.19221931)
('59431675b1ec1308509ffff7', 'Ohana Hibachi Steak & Seafood', 40.828645, -73.824702, '3604 East Tremont Avenue, New York, NY 10465, United States', 262, True, -5801976.493478547, 9846815.35729968)
('54de4db5498ee465b7d151d2', 'Sarku Japan', 40.828769832278994, -73.84824397798991, '815 Hutchinson River Pkwy, Bronx, NY 10465, United States', 223, True, -5802048.897085469, 9849842.136940122)
('4dba07b7fa8c2e303f1b124f', 'Yama Asian Bistro', 40.658578000000006, -73.982259, '268 Prospect Park W, Brooklyn, NY 11215, United States', 258, True, -5831399.698996186, 9866288.943536613)
('51f9b7b3498eefe896caeb23', 'Shalom Japan', 40.709219, -73.955839, '310 S 4th St (at Rodney St), Brooklyn, NY 11211, United States', 258, True, -5822710.210909358, 9863111.155610856)
('

In [20]:
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=11)
folium.Marker([latitude, longitude]).add_to(map_newyork)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_japanese = res[6]
    color = 'red' if is_japanese else 'blue'
    folium.CircleMarker([lat, lon], radius=2, color=color, fill=True, fill_color=color, fill_opacity=0.7).add_to(map_newyork)
map_newyork

In [21]:
distance_from_center = []
x11 = []
y11 = []

for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    
    x1, y1 = lonlat_to_xy(lng, lat)
    distance = calc_xy_distance(x, y, x1, y1)
    distance_from_center.append(distance)
    x11.append(x1)
    y11.append(y1)

location_restaurants_count = [len(res) for res in location_restaurants]

neighborhoods['Distance from center'] = distance_from_center
neighborhoods['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

neighborhoods

Average number of restaurants in every area with radius=300m: 4.598039215686274


Borough               Neighborhood   Latitude  Longitude  \
0            Bronx                  Wakefield  40.894705 -73.847201   
1            Bronx                 Co-op City  40.874294 -73.829939   
2            Bronx                Eastchester  40.887556 -73.827806   
3            Bronx                  Fieldston  40.895437 -73.905643   
4            Bronx                  Riverdale  40.890834 -73.912585   
5            Bronx                Kingsbridge  40.881687 -73.902818   
6        Manhattan                Marble Hill  40.876551 -73.910660   
7            Bronx                   Woodlawn  40.898273 -73.867315   
8            Bronx                    Norwood  40.877224 -73.879391   
9            Bronx             Williamsbridge  40.881039 -73.857446   
10           Bronx                 Baychester  40.866858 -73.835798   
11           Bronx             Pelham Parkway  40.857413 -73.854756   
12           Bronx                City Island  40.847247 -73.786488   
13           Bronx               Bedford Park  40.870185 -73.885512   
14           Bronx         University Heights  40.855727 -73.910416   
15           Bronx             Morris Heights  40.847898 -73.919672   
16           Bronx                    Fordham  40.860997 -73.896427   
17           Bronx               East Tremont  40.842696 -73.887356   
18           Bronx                 West Farms  40.839475 -73.877745   
19           Bronx               High  Bridge  40.836623 -73.926102   
20           Bronx                    Melrose  40.819754 -73.909422   
21           Bronx                 Mott Haven  40.806239 -73.916100   
22           Bronx                Port Morris  40.801664 -73.913221   
23           Bronx                   Longwood  40.815099 -73.895788   
24           Bronx                Hunts Point  40.809730 -73.883315   
25           Bronx                 Morrisania  40.823592 -73.901506   
26           Bronx                  Soundview  40.821012 -73.865746   
27           Bronx               Clason Point  40.806551 -73.854144   
28           Bronx                Throgs Neck  40.815109 -73.816350   
29           Bronx               Country Club  40.844246 -73.824099   
30           Bronx                Parkchester  40.837938 -73.856003   
31           Bronx         Westchester Square  40.840619 -73.842194   
32           Bronx                   Van Nest  40.843608 -73.866299   
33           Bronx                Morris Park  40.847549 -73.850402   
34           Bronx                    Belmont  40.857277 -73.888452   
35           Bronx             Spuyten Duyvil  40.881395 -73.917190   
36           Bronx            North Riverdale  40.908543 -73.904531   
37           Bronx                 Pelham Bay  40.850641 -73.832074   
38           Bronx              Schuylerville  40.826580 -73.826203   
39           Bronx             Edgewater Park  40.821986 -73.813885   
40           Bronx                Castle Hill  40.819014 -73.848027   
41           Bronx                  Olinville  40.871371 -73.863324   
42           Bronx             Pelham Gardens  40.862966 -73.841612   
43           Bronx                  Concourse  40.834284 -73.915589   
44           Bronx                  Unionport  40.829774 -73.850535   
45           Bronx                   Edenwald  40.884561 -73.848083   
46        Brooklyn                  Bay Ridge  40.625801 -74.030621   
47        Brooklyn                Bensonhurst  40.611009 -73.995180   
48        Brooklyn                Sunset Park  40.645103 -74.010316   
49        Brooklyn                 Greenpoint  40.730201 -73.954241   
50        Brooklyn                  Gravesend  40.595260 -73.973471   
51        Brooklyn             Brighton Beach  40.576825 -73.965094   
52        Brooklyn             Sheepshead Bay  40.586890 -73.943186   
53        Brooklyn          Manhattan Terrace  40.614433 -73.957438   
54        Brooklyn                   Flatbush  40.636326 -73.958401   
55        Brooklyn              Cro

In [22]:
distances_to_japanese_restaurant = []
   
for area_x, area_y in zip(x11, y11):
    min_distance = 10000
    for res in japanese_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_japanese_restaurant.append(min_distance)

neighborhoods['Distance to japanese restaurant'] = distances_to_japanese_restaurant
neighborhoods['X'] = x11
neighborhoods['Y'] = y11

neighborhoods

Borough               Neighborhood   Latitude  Longitude  \
0            Bronx                  Wakefield  40.894705 -73.847201   
1            Bronx                 Co-op City  40.874294 -73.829939   
2            Bronx                Eastchester  40.887556 -73.827806   
3            Bronx                  Fieldston  40.895437 -73.905643   
4            Bronx                  Riverdale  40.890834 -73.912585   
5            Bronx                Kingsbridge  40.881687 -73.902818   
6        Manhattan                Marble Hill  40.876551 -73.910660   
7            Bronx                   Woodlawn  40.898273 -73.867315   
8            Bronx                    Norwood  40.877224 -73.879391   
9            Bronx             Williamsbridge  40.881039 -73.857446   
10           Bronx                 Baychester  40.866858 -73.835798   
11           Bronx             Pelham Parkway  40.857413 -73.854756   
12           Bronx                City Island  40.847247 -73.786488   
13           Bronx               Bedford Park  40.870185 -73.885512   
14           Bronx         University Heights  40.855727 -73.910416   
15           Bronx             Morris Heights  40.847898 -73.919672   
16           Bronx                    Fordham  40.860997 -73.896427   
17           Bronx               East Tremont  40.842696 -73.887356   
18           Bronx                 West Farms  40.839475 -73.877745   
19           Bronx               High  Bridge  40.836623 -73.926102   
20           Bronx                    Melrose  40.819754 -73.909422   
21           Bronx                 Mott Haven  40.806239 -73.916100   
22           Bronx                Port Morris  40.801664 -73.913221   
23           Bronx                   Longwood  40.815099 -73.895788   
24           Bronx                Hunts Point  40.809730 -73.883315   
25           Bronx                 Morrisania  40.823592 -73.901506   
26           Bronx                  Soundview  40.821012 -73.865746   
27           Bronx               Clason Point  40.806551 -73.854144   
28           Bronx                Throgs Neck  40.815109 -73.816350   
29           Bronx               Country Club  40.844246 -73.824099   
30           Bronx                Parkchester  40.837938 -73.856003   
31           Bronx         Westchester Square  40.840619 -73.842194   
32           Bronx                   Van Nest  40.843608 -73.866299   
33           Bronx                Morris Park  40.847549 -73.850402   
34           Bronx                    Belmont  40.857277 -73.888452   
35           Bronx             Spuyten Duyvil  40.881395 -73.917190   
36           Bronx            North Riverdale  40.908543 -73.904531   
37           Bronx                 Pelham Bay  40.850641 -73.832074   
38           Bronx              Schuylerville  40.826580 -73.826203   
39           Bronx             Edgewater Park  40.821986 -73.813885   
40           Bronx                Castle Hill  40.819014 -73.848027   
41           Bronx                  Olinville  40.871371 -73.863324   
42           Bronx             Pelham Gardens  40.862966 -73.841612   
43           Bronx                  Concourse  40.834284 -73.915589   
44           Bronx                  Unionport  40.829774 -73.850535   
45           Bronx                   Edenwald  40.884561 -73.848083   
46        Brooklyn                  Bay Ridge  40.625801 -74.030621   
47        Brooklyn                Bensonhurst  40.611009 -73.995180   
48        Brooklyn                Sunset Park  40.645103 -74.010316   
49        Brooklyn                 Greenpoint  40.730201 -73.954241   
50        Brooklyn                  Gravesend  40.595260 -73.973471   
51        Brooklyn             Brighton Beach  40.576825 -73.965094   
52        Brooklyn             Sheepshead Bay  40.586890 -73.943186   
53        Brooklyn          Manhattan Terrace  40.614433 -73.957438   
54        Brooklyn                   Flatbush  40.636326 -73.958401   
55        Brooklyn              Cro

In [23]:
print('Average distance to closest japanese restaurant from each area center:', neighborhoods['Distance to japanese restaurant'].mean())

Average distance to closest japanese restaurant from each area center: 3276.5423534060956


In [24]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

japanese_latlons = [[res[2], res[3]] for res in japanese_restaurants.values()]

In [25]:
from folium import plugins
from folium.plugins import HeatMap

map_newyork = folium.Map(location=[latitude, longitude], zoom_start=11)
folium.TileLayer('cartodbpositron').add_to(map_newyork) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_newyork)
folium.Marker([latitude, longitude]).add_to(map_newyork)
folium.Circle([latitude, longitude], radius=1000, fill=False, color='white').add_to(map_newyork)
folium.Circle([latitude, longitude], radius=2000, fill=False, color='white').add_to(map_newyork)
folium.Circle([latitude, longitude], radius=3000, fill=False, color='white').add_to(map_newyork)
map_newyork

In [26]:
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=11)
folium.TileLayer('cartodbpositron').add_to(map_newyork) #cartodbpositron cartodbdark_matter
HeatMap(japanese_latlons).add_to(map_newyork)
folium.Marker([latitude, longitude]).add_to(map_newyork)
folium.Circle([latitude, longitude], radius=1000, fill=False, color='white').add_to(map_newyork)
folium.Circle([latitude, longitude], radius=2000, fill=False, color='white').add_to(map_newyork)
folium.Circle([latitude, longitude], radius=3000, fill=False, color='white').add_to(map_newyork)
map_newyork

In [27]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data

Borough         Neighborhood   Latitude  Longitude  \
0   Manhattan          Marble Hill  40.876551 -73.910660   
1   Manhattan            Chinatown  40.715618 -73.994279   
2   Manhattan   Washington Heights  40.851903 -73.936900   
3   Manhattan               Inwood  40.867684 -73.921210   
4   Manhattan     Hamilton Heights  40.823604 -73.949688   
5   Manhattan       Manhattanville  40.816934 -73.957385   
6   Manhattan       Central Harlem  40.815976 -73.943211   
7   Manhattan          East Harlem  40.792249 -73.944182   
8   Manhattan      Upper East Side  40.775639 -73.960508   
9   Manhattan            Yorkville  40.775930 -73.947118   
10  Manhattan           Lenox Hill  40.768113 -73.958860   
11  Manhattan     Roosevelt Island  40.762160 -73.949168   
12  Manhattan      Upper West Side  40.787658 -73.977059   
13  Manhattan       Lincoln Square  40.773529 -73.985338   
14  Manhattan              Clinton  40.759101 -73.996119   
15  Manhattan              Midtown  40.754691 -73.981669   
16  Manhattan          Murray Hill  40.748303 -73.978332   
17  Manhattan              Chelsea  40.744035 -74.003116   
18  Manhattan    Greenwich Village  40.726933 -73.999914   
19  Manhattan         East Village  40.727847 -73.982226   
20  Manhattan      Lower East Side  40.717807 -73.980890   
21  Manhattan              Tribeca  40.721522 -74.010683   
22  Manhattan         Little Italy  40.719324 -73.997305   
23  Manhattan                 Soho  40.722184 -74.000657   
24  Manhattan         West Village  40.734434 -74.006180   
25  Manhattan     Manhattan Valley  40.797307 -73.964286   
26  Manhattan  Morningside Heights  40.808000 -73.963896   
27  Manhattan             Gramercy  40.737210 -73.981376   
28  Manhattan    Battery Park City  40.711932 -74.016869   
29  Manhattan   Financial District  40.707107 -74.010665   
30  Manhattan        Carnegie Hill  40.782683 -73.953256   
31  Manhattan                 Noho  40.723259 -73.988434   
32  Manhattan         Civic Center  40.715229 -74.005415   
33  Manhattan        Midtown South  40.748510 -73.988713   
34  Manhattan         Sutton Place  40.760280 -73.963556   
35  Manhattan           Turtle Bay  40.752042 -73.967708   
36  Manhattan           Tudor City  40.746917 -73.971219   
37  Manhattan      Stuyvesant Town  40.731000 -73.974052   
38  Manhattan             Flatiron  40.739673 -73.990947   
39  Manhattan         Hudson Yards  40.756658 -74.000111   

    Distance from center  Restaurants in area  \
0           30350.889260                    2   
1            1592.829596                   61   
2           25210.649467                    8   
3           28437.332611                    8   
4           20148.983287                    5   
5           18745.338688                    7   
6           19285.291507                    1   
7           15665.673376                    6   
8           12177.841311                    4   
9           13138.292821                   14   
10          11191.743146                   19   
11          11139.996171                    3   
12          13244.062702                    9   
13          10651.506266                    3   
14           7969.161533                    7   
15           7780.903783                   23   
16           7013.358877                   36   
17           5324.492462                   19   
18           2535.763787                   27   
19           4001.647520                   63   
20           3356.722062                    1   
21           1609.383898                    3   
22           1586.730780                   55   
23           1747.367028                    4   
24           3682.923779                   13   
25          15317.723204                    7   
26          17041.207268                    6   
27           5231.481437                   21   
28           1408.164099                    3   
29           1127.281841                   23   
30          13676.431787  

In [28]:
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude_m = location.latitude
longitude_m = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude_m, longitude_m))

The geograpical coordinate of Manhattan are 40.7896239, -73.9598939.


In [29]:
map_manhattan = folium.Map(location=[latitude_m, longitude_m], zoom_start=12)

for lat, lng, label in zip(manhattan_data['Latitude'], manhattan_data['Longitude'], manhattan_data['Neighborhood']):
    folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_manhattan)  
map_manhattan

In [30]:
x22 = []
y22 = []

for lat, lng in zip(manhattan_data['Latitude'], manhattan_data['Longitude']):
    x2, y2 = lonlat_to_xy(lng, lat)
    x22.append(x2)
    y22.append(y2)

In [31]:
def count_restaurants_nearby(x, y, restaurants, radius):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 10000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_japanese_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(x22, y22):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, japanese_restaurants)
    roi_japanese_distances.append(distance)
print('done.')

Generating data on location candidates... done.


In [32]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Neighborhood':manhattan_data['Neighborhood'],
                                 'Latitude':manhattan_data['Latitude'],
                                 'Longitude':manhattan_data['Longitude'],
                                 'X':x22,
                                 'Y':y22,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Japanese restaurant':roi_japanese_distances})

df_roi_locations

Neighborhood   Latitude  Longitude             X             Y  \
0           Marble Hill  40.876551 -73.910660 -5.794205e+06  9.858099e+06   
1             Chinatown  40.715618 -73.994279 -5.821760e+06  9.868103e+06   
2    Washington Heights  40.851903 -73.936900 -5.798470e+06  9.861349e+06   
3                Inwood  40.867684 -73.921210 -5.795743e+06  9.859410e+06   
4      Hamilton Heights  40.823604 -73.949688 -5.803305e+06  9.862859e+06   
5        Manhattanville  40.816934 -73.957385 -5.804461e+06  9.863817e+06   
6        Central Harlem  40.815976 -73.943211 -5.804573e+06  9.861989e+06   
7           East Harlem  40.792249 -73.944182 -5.808594e+06  9.862002e+06   
8       Upper East Side  40.775639 -73.960508 -5.811466e+06  9.864025e+06   
9             Yorkville  40.775930 -73.947118 -5.811369e+06  9.862302e+06   
10           Lenox Hill  40.768113 -73.958860 -5.812735e+06  9.863778e+06   
11     Roosevelt Island  40.762160 -73.949168 -5.813710e+06  9.862501e+06   
12      Upper West Side  40.787658 -73.977059 -5.809488e+06  9.866213e+06   
13       Lincoln Square  40.773529 -73.985338 -5.811911e+06  9.867214e+06   
14              Clinton  40.759101 -73.996119 -5.814393e+06  9.868537e+06   
15              Midtown  40.754691 -73.981669 -5.815091e+06  9.866655e+06   
16          Murray Hill  40.748303 -73.978332 -5.816162e+06  9.866195e+06   
17              Chelsea  40.744035 -74.003116 -5.816971e+06  9.869371e+06   
18    Greenwich Village  40.726933 -73.999914 -5.819860e+06  9.868881e+06   
19         East Village  40.727847 -73.982226 -5.819644e+06  9.866603e+06   
20      Lower East Side  40.717807 -73.980890 -5.821342e+06  9.866385e+06   
21              Tribeca  40.721522 -74.010683 -5.820815e+06  9.870247e+06   
22         Little Italy  40.719324 -73.997305 -5.821142e+06  9.868510e+06   
23                 Soho  40.722184 -74.000657 -5.820668e+06  9.868956e+06   
24         West Village  40.734434 -74.006180 -5.818610e+06  9.869723e+06   
25     Manhattan Valley  40.797307 -73.964286 -5.807809e+06  9.864613e+06   
26  Morningside Heights  40.808000 -73.963896 -5.805997e+06  9.864613e+06   
27             Gramercy  40.737210 -73.981376 -5.818053e+06  9.866537e+06   
28    Battery Park City  40.711932 -74.016869 -5.822463e+06  9.871002e+06   
29   Financial District  40.707107 -74.010665 -5.823260e+06  9.870180e+06   
30        Carnegie Hill  40.782683 -73.953256 -5.810247e+06  9.863125e+06   
31                 Noho  40.723259 -73.988434 -5.820444e+06  9.867383e+06   
32         Civic Center  40.715229 -74.005415 -5.821864e+06  9.869539e+06   
33        Midtown South  40.748510 -73.988713 -5.816163e+06  9.867535e+06   
34         Sutton Place  40.760280 -73.963556 -5.814080e+06  9.864346e+06   
35           Turtle Bay  40.752042 -73.967708 -5.815491e+06  9.864843e+06   
36           Tudor City  40.746917 -73.971219 -5.816372e+06  9.865272e+06   
37      Stuyvesant Town  40.731000 -73.974052 -5.819081e+06  9.865563e+06   
38             Flatiron  40.739673 -73.990947 -5.817669e+06  9.867782e+06   
39         Hudson Yards  40.756658 -74.000111 -5.814821e+06  9.869041e+06   

    Restaurants nearby  Distance to Japanese restaurant  
0                    0                       936.954860  
1                   14                       285.595012  
2                    2                      5050.983170  
3                    6                      1906.860027  
4                    0                       322.633489  
5                    1                      1435.325988  
6                    0                      1813.753790  
7                    2                      3833.052588  
8                    0                       349.602430  
9                    1                      1666.612974  
10                   8                       226.026731  
11                   3                      1168.770896  
12                   3                       366.602033  
13                   1                   

In [33]:
good_restaurant_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_restaurant_count.sum())

good_japanese_distance = np.array(df_roi_locations['Distance to Japanese restaurant']>=400)
print('Locations with no Japanese restaurants within 400m:', good_japanese_distance.sum())

good_locations = np.logical_and(good_restaurant_count, good_japanese_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]

Locations with no more than two restaurants nearby: 22
Locations with no Japanese restaurants within 400m: 20
Locations with both conditions met: 17


In [34]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values
good_neighborhood = df_good_locations['Neighborhood'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_manhattan = folium.Map(location=[latitude_m, longitude_m], zoom_start=12)
folium.TileLayer('cartodbpositron').add_to(map_manhattan)
HeatMap(restaurant_latlons).add_to(map_manhattan)
folium.Circle([latitude_m, longitude_m], radius=1000, fill=False, color='white').add_to(map_manhattan)
folium.Circle([latitude_m, longitude_m], radius=2000, fill=False, color='white').add_to(map_manhattan)
folium.Circle([latitude_m, longitude_m], radius=3000, fill=False, color='white').add_to(map_manhattan)
folium.Circle([latitude_m, longitude_m], radius=3000, color='white', fill=True, fill_opacity=0.6).add_to(map_manhattan)
folium.Marker([latitude, longitude]).add_to(map_manhattan)
for lat, lon, label in zip(good_latitudes, good_longitudes, good_neighborhood):
    folium.Popup(label)
    folium.CircleMarker([lat, lon], radius=5, popup=label, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_manhattan) 
map_manhattan

In [35]:
from sklearn.cluster import KMeans

number_of_clusters = 5

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_manhattan = folium.Map(location=[latitude_m, longitude_m], zoom_start=12)
folium.TileLayer('cartodbpositron').add_to(map_manhattan)
HeatMap(restaurant_latlons).add_to(map_manhattan)
folium.Circle([latitude_m, longitude_m], radius=1000, fill=False, color='white').add_to(map_manhattan)
folium.Circle([latitude_m, longitude_m], radius=2000, fill=False, color='white').add_to(map_manhattan)
folium.Circle([latitude_m, longitude_m], radius=3000, fill=False, color='white').add_to(map_manhattan)
folium.Circle([latitude_m, longitude_m], radius=3000, color='white', fill=True, fill_opacity=0.4).add_to(map_manhattan)
folium.Marker([latitude, longitude]).add_to(map_manhattan)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=2500, color='green', fill=True, fill_opacity=0.25).add_to(map_manhattan) 
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_japanese = res[6]
    color = 'red' if is_japanese else 'blue'
    folium.CircleMarker([lat, lon], radius=2, color=color, fill=True, fill_color=color, fill_opacity=0.7).add_to(map_manhattan) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=5, color='yellow', fill=True, fill_color='yellow', fill_opacity=0.7).add_to(map_manhattan)
map_manhattan

In [36]:
map_manhattan = folium.Map(location=[latitude_m, longitude_m], zoom_start=15)
folium.Circle([latitude_m, longitude_m], radius=1000, fill=False, color='white').add_to(map_manhattan)
folium.Circle([latitude_m, longitude_m], radius=2000, fill=False, color='white').add_to(map_manhattan)
folium.Circle([latitude_m, longitude_m], radius=3000, fill=False, color='white').add_to(map_manhattan)
folium.Circle([latitude_m, longitude_m], radius=3000, color='white', fill=True, fill_opacity=0.4).add_to(map_manhattan)
folium.Marker([latitude, longitude]).add_to(map_manhattan)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=2500, color='green', fill=True, fill_opacity=0.25).add_to(map_manhattan) 
for res in restaurants.values():
    label = folium.Popup(res[1])
    lat = res[2]; lon = res[3]
    is_japanese = res[6]
    color = 'red' if is_japanese else 'blue'
    folium.CircleMarker([lat, lon], radius=5, popup= label, color=color, fill=True, fill_color=color, fill_opacity=0.7).add_to(map_manhattan) 
for lat, lon, label in zip(good_latitudes, good_longitudes, good_neighborhood):
    folium.Popup(label)
    folium.CircleMarker([lat, lon], radius=10, popup=label, color='yellow', fill=True, fill_color='yellow', fill_opacity=0.7).add_to(map_manhattan)
map_manhattan